## Ejercicio 1: Recopilación de datos. (1p)

Se deben recopilar más de 5000 tweets en inglés que puedan tener un sentimiento positivo, 
negativo o neutro. Procurar mantener en la medida de lo posible una proporción equilibrada. Para la
recopilación de los datos se puede hacer de forma manual (no recomendable) o usar un dataset de 
tweets de la base de datos Kaggle (OJO! Que el texto no esté ya pre-procesado). Los tweets 
recopilados se deben almacenar en un archivo CSV que se debe leer con pandas. Muestra en el 
notebook las primeras 5 filas de la tabla leída.

In [38]:
#Se cargan todas las librerías que vamos a usar

import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix
from sklearn.pipeline import make_pipeline

import nltk
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from nltk.tokenize import TweetTokenizer
import re
from nltk.stem import SnowballStemmer
from textblob import TextBlob


In [2]:
tweets = pd.read_csv('Tweets.csv')
tweets=tweets["text"]
tweets.head(5)

0                  @VirginAmerica What @dhepburn said.
1    @VirginAmerica plus you've added commercials t...
2    @VirginAmerica I didn't today... Must mean I n...
3    @VirginAmerica it's really aggressive to blast...
4    @VirginAmerica and it's a really big bad thing...
Name: text, dtype: object

In [9]:
tweets.head(15)

0                   @VirginAmerica What @dhepburn said.
1     @VirginAmerica plus you've added commercials t...
2     @VirginAmerica I didn't today... Must mean I n...
3     @VirginAmerica it's really aggressive to blast...
4     @VirginAmerica and it's a really big bad thing...
5     @VirginAmerica seriously would pay $30 a fligh...
6     @VirginAmerica yes, nearly every time I fly VX...
7     @VirginAmerica Really missed a prime opportuni...
8       @virginamerica Well, I didn't…but NOW I DO! :-D
9     @VirginAmerica it was amazing, and arrived an ...
10    @VirginAmerica did you know that suicide is th...
11    @VirginAmerica I &lt;3 pretty graphics. so muc...
12    @VirginAmerica This is such a great deal! Alre...
13    @VirginAmerica @virginmedia I'm flying your #f...
14                               @VirginAmerica Thanks!
Name: text, dtype: object

In [ ]:
# Para el ejercicio debemos quedarnos con la columna "text".


## Ejercicio 2: Limpieza del texto, eliminar las palabras que no aportan información. (2p)

Crear una función limpiar_texto que toma un dataset como entrada y realiza una serie de 
pasos de preprocesamiento para limpiar y estructurar el texto de manera que sea más adecuado para 
tareas de procesamiento de lenguaje natural (NLP). 
Para cada línea de texto del data set, la función debe:
* Eliminar menciones, hashtags y URLs del texto. Pista: la función re.sub() puede ser útil.
* Convertir el texto en minúscula.
* Separa las palabras dentro del tweet como elementos de una lista. A este proceso se le llama tokenización, investiga cómo hacerlo con la función TweetTokenizer() incluida en NLTK.
* Para cada una de las palabras en esa lista generada:
    * Eliminar las palabras comunes y poco informativas (conocidas como stop words). Usa la recopilación de stop words que ya existe en NLTK (accede a ellas con stopwords.words() seleccionando inglés como idioma).
    * Utilizar técnicas de lematización (stemming). Investiga qué son y usa el modelo SnowballStemmer() que ya incluye NLTK para stemming.
* Transformar la lista final en una cadena de caracteres de nuevo. Cada palabra debe estar separada por un espacio y ese texto debe sustituir al original en la tabla del dataset.

In [24]:
def limpiar_texto(dataset):
    for n in range(0,len(dataset)-1):
        texto_limpio = re.sub(r"@\w+|#\w+|https?://\S+|www\.\S+|[\U0001F600-\U0001F64F\U0001F300-\U0001F5FF\U0001F680-\U0001F6FF\U0001F700-\U0001F77F\U0001F780-\U0001F7FF\U0001F800-\U0001F8FF\U0001F900-\U0001F9FF\U0001FA00-\U0001FA6F\U0001FA70-\U0001FAFF\U00002702-\U000027B0\U000024C2-\U0001F251]+","",dataset[n])
        texto_minusculas = texto_limpio.lower()
        tokenizer = TweetTokenizer()
        texto_separado = tokenizer.tokenize(texto_minusculas)
        
        stop_words = set(stopwords.words('english'))
        
        texto_filtrado = []
        for palabra in texto_separado:
            if palabra not in stop_words:
                texto_filtrado.append(palabra)
            
            lematizacion = SnowballStemmer("english")
            lexemas = [lematizacion.stem(palabra) for palabra in texto_filtrado]
        
        texto_final = " ".join(lexemas)
        dataset[n]=texto_final
    
    return dataset
                
            

In [25]:
limpiar_texto(tweets)

0                                                   said .
1                      plus ad commerci experi ... tacki .
2               today ... must mean need take anoth trip !
3        realli aggress blast obnoxi " entertain " gues...
4                                     realli big bad thing
                               ...                        
14635                    thank got differ flight chicago .
14636    leav 20 minut late flight . warn communic 15 m...
14637                           plea bring american airlin
14638    money , chang flight , answer phone ! suggest ...
14639    @AmericanAir we have 8 ppl so we need 2 know h...
Name: text, Length: 14640, dtype: object

## Ejercicio3: Etiquetado de datos con herramientas ya existentes. (2p)
El objetivo principal de esta función es asignar la categoría de sentimiento correspondiente usando modelos existentes como TextBlob. TextBlob asigna una puntuación de polaridad al texto, donde valores positivos indican sentimientos positivos y valores negativos indican sentimientos negativos. La intención del proyecto es usar los modelos ya existentes para crear el dataset de entrenamiento necesario para entrenar nuestro propio modelo e intentar que funcione mejor que los ya existentes. Define una función llamada clasificador que toma el dataset con el texto procesado y limpio como entrada. El resultado de este proceso debe almacenarse en un archivo CSV con dos columnas: una para la frase o texto y otra para la etiqueta correspondiente.
* Para cada línea de texto del data set, la función debe:
    * Utilizar el modelo TextBlob para realizar un análisis de sentimiento. Investiga cómo hacerlo.
    * En función de la polaridad calculada, clasificar el sentimiento en categorías específicas. Las categorías deben incluir "Contento", "Muy feliz", "Neutro", "Molesto" y "Hater".
* Finalmente, guardar los resultados como una columna nueva en el dataset.

In [43]:
def clasificador(data):
    for fila in data:
        blob = TextBlob(fila)
        polaridad,subjetividad = blob.sentiment
        if polaridad == 0:
            data["sentimiento"]= "Neutro"
        elif polaridad > 0 and polaridad < 0.5:
            data["sentimiento"]= "Contento"
        elif polaridad >= 0.5 and polaridad < 1:
            data["sentimiento"]= "Muy feliz"
        elif polaridad < 0 and polaridad > -0.5:
            data["sentimiento"]= "Molesto"
        elif polaridad < -0.5 and polaridad > -1:
            data["sentimiento"]= "Hater"
        
        print(data)
    
        
        

In [44]:
clasificador(tweets)

0                                                         said .
1                            plus ad commerci experi ... tacki .
2                     today ... must mean need take anoth trip !
3              realli aggress blast obnoxi " entertain " gues...
4                                           realli big bad thing
                                     ...                        
14636          leav 20 minut late flight . warn communic 15 m...
14637                                 plea bring american airlin
14638          money , chang flight , answer phone ! suggest ...
14639          @AmericanAir we have 8 ppl so we need 2 know h...
sentimiento                                               Neutro
Name: text, Length: 14641, dtype: object
0                                                         said .
1                            plus ad commerci experi ... tacki .
2                     today ... must mean need take anoth trip !
3              realli aggress blast obnoxi " ente

0                                                         said .
1                            plus ad commerci experi ... tacki .
2                     today ... must mean need take anoth trip !
3              realli aggress blast obnoxi " entertain " gues...
4                                           realli big bad thing
                                     ...                        
14636          leav 20 minut late flight . warn communic 15 m...
14637                                 plea bring american airlin
14638          money , chang flight , answer phone ! suggest ...
14639          @AmericanAir we have 8 ppl so we need 2 know h...
sentimiento                                               Neutro
Name: text, Length: 14641, dtype: object
0                                                         said .
1                            plus ad commerci experi ... tacki .
2                     today ... must mean need take anoth trip !
3              realli aggress blast obnoxi " ente

0                                                         said .
1                            plus ad commerci experi ... tacki .
2                     today ... must mean need take anoth trip !
3              realli aggress blast obnoxi " entertain " gues...
4                                           realli big bad thing
                                     ...                        
14636          leav 20 minut late flight . warn communic 15 m...
14637                                 plea bring american airlin
14638          money , chang flight , answer phone ! suggest ...
14639          @AmericanAir we have 8 ppl so we need 2 know h...
sentimiento                                               Neutro
Name: text, Length: 14641, dtype: object
0                                                         said .
1                            plus ad commerci experi ... tacki .
2                     today ... must mean need take anoth trip !
3              realli aggress blast obnoxi " ente

0                                                         said .
1                            plus ad commerci experi ... tacki .
2                     today ... must mean need take anoth trip !
3              realli aggress blast obnoxi " entertain " gues...
4                                           realli big bad thing
                                     ...                        
14636          leav 20 minut late flight . warn communic 15 m...
14637                                 plea bring american airlin
14638          money , chang flight , answer phone ! suggest ...
14639          @AmericanAir we have 8 ppl so we need 2 know h...
sentimiento                                               Neutro
Name: text, Length: 14641, dtype: object
0                                                         said .
1                            plus ad commerci experi ... tacki .
2                     today ... must mean need take anoth trip !
3              realli aggress blast obnoxi " ente

0                                                         said .
1                            plus ad commerci experi ... tacki .
2                     today ... must mean need take anoth trip !
3              realli aggress blast obnoxi " entertain " gues...
4                                           realli big bad thing
                                     ...                        
14636          leav 20 minut late flight . warn communic 15 m...
14637                                 plea bring american airlin
14638          money , chang flight , answer phone ! suggest ...
14639          @AmericanAir we have 8 ppl so we need 2 know h...
sentimiento                                               Neutro
Name: text, Length: 14641, dtype: object
0                                                         said .
1                            plus ad commerci experi ... tacki .
2                     today ... must mean need take anoth trip !
3              realli aggress blast obnoxi " ente

...

0                                                         said .
1                            plus ad commerci experi ... tacki .
2                     today ... must mean need take anoth trip !
3              realli aggress blast obnoxi " entertain " gues...
4                                           realli big bad thing
                                     ...                        
14636          leav 20 minut late flight . warn communic 15 m...
14637                                 plea bring american airlin
14638          money , chang flight , answer phone ! suggest ...
14639          @AmericanAir we have 8 ppl so we need 2 know h...
sentimiento                                              Molesto
Name: text, Length: 14641, dtype: object
0                                                         said .
1                            plus ad commerci experi ... tacki .
2                     today ... must mean need take anoth trip !
3              realli aggress blast obnoxi " ente

0                                                         said .
1                            plus ad commerci experi ... tacki .
2                     today ... must mean need take anoth trip !
3              realli aggress blast obnoxi " entertain " gues...
4                                           realli big bad thing
                                     ...                        
14636          leav 20 minut late flight . warn communic 15 m...
14637                                 plea bring american airlin
14638          money , chang flight , answer phone ! suggest ...
14639          @AmericanAir we have 8 ppl so we need 2 know h...
sentimiento                                               Neutro
Name: text, Length: 14641, dtype: object
0                                                         said .
1                            plus ad commerci experi ... tacki .
2                     today ... must mean need take anoth trip !
3              realli aggress blast obnoxi " ente

0                                                         said .
1                            plus ad commerci experi ... tacki .
2                     today ... must mean need take anoth trip !
3              realli aggress blast obnoxi " entertain " gues...
4                                           realli big bad thing
                                     ...                        
14636          leav 20 minut late flight . warn communic 15 m...
14637                                 plea bring american airlin
14638          money , chang flight , answer phone ! suggest ...
14639          @AmericanAir we have 8 ppl so we need 2 know h...
sentimiento                                               Neutro
Name: text, Length: 14641, dtype: object
0                                                         said .
1                            plus ad commerci experi ... tacki .
2                     today ... must mean need take anoth trip !
3              realli aggress blast obnoxi " ente

0                                                         said .
1                            plus ad commerci experi ... tacki .
2                     today ... must mean need take anoth trip !
3              realli aggress blast obnoxi " entertain " gues...
4                                           realli big bad thing
                                     ...                        
14636          leav 20 minut late flight . warn communic 15 m...
14637                                 plea bring american airlin
14638          money , chang flight , answer phone ! suggest ...
14639          @AmericanAir we have 8 ppl so we need 2 know h...
sentimiento                                               Neutro
Name: text, Length: 14641, dtype: object
0                                                         said .
1                            plus ad commerci experi ... tacki .
2                     today ... must mean need take anoth trip !
3              realli aggress blast obnoxi " ente

KeyboardInterrupt: 

In [42]:
from nltk.corpus import stopwords
nltk.download('stopwords')
from nltk.stem import PorterStemmer
from nltk.tokenize import TweetTokenizer

frase = "hello i am Vincent and i like to play tennis"
tokenizer = TweetTokenizer()
frase_sep = tokenizer.tokenize(frase)
stop_words = stopwords.words('english')
for n in frase_sep:
    if n not in stop_words:
        frase_sep[n] = frase_sep[n]

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\ASUS\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


TypeError: list indices must be integers or slices, not str

In [7]:

import re
string = "What @dhepburn said about #flight_delays. Check it on www.american-airlines.com and subscribe to https://ev.us.es"
new_string = re.sub(r"@\w+|#\w+|https?://\S+|www\.\S+","",string)
print(new_string)

What  said about . Check it on  and subscribe to 


In [40]:
ejemplo = "Me encanta utilizar TextBlob para el análisis de sentimientos."
ejemplo2= "Odio a mi vecino, lo quiero matar de la peor manera posible."
ejemplo3= "Te amo cariño, soy muy feliz de tenerte."
blob = TextBlob(ejemplo2)

polaridad,subjetividad = blob.sentiment
print(polaridad,subjetividad)

if polaridad > 0:
    print("El texto es positivo.")
elif polaridad < 0:
    print("El texto es negativo.")
else:
    print("El texto es neutral.")

print(f"Polaridad: {polaridad}, Subjetividad: {subjetividad}")

0.0 0.0
El texto es neutral.
Polaridad: 0.0, Subjetividad: 0.0
